In [1]:
# Importando as bibliotecas
from nltk.tokenize import TweetTokenizer
import nltk
import re
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn import metrics
from sklearn.model_selection import cross_val_predict
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score

tweet_tokenizer = TweetTokenizer() 

In [33]:
# Lendo base de dados
tweets_minas = pd.read_csv('C:/Users/GUILHERME/Desktop/Análise de Sentimentos/Datasets/Classificados/tweets_mg.csv', encoding='utf-8')

In [34]:
# Distribuição das classes da coluna ‘Classificação’:
tweets_minas.Classificacao.value_counts()

Positivo    3300
Neutro      2453
Negativo    2446
Name: Classificacao, dtype: int64

In [35]:
#Removendo valores neutros
tweets_minas = df.loc[(df['Classificacao'] == 'Neutro')]
tweets_minas = df.drop(tweets_minas.index)
tweets_minas.head()

Text Classificacao
4   ��� PSOL vai questionar aumento de vereadores ...      Negativo
8   "BB e governo de Minas travam disputa sobre de...      Negativo
12  "erro desconhecido" é mato! Aliás, é da secret...      Negativo
16  "Mesmo sem muito dinheiro no caixa o governo d...      Negativo
25  "uso de aeronave pertencente ao  Estado de MG,...      Negativo

In [36]:
#Substituindo valores de string por números para ficar mais compatível com o base de teste. 1 para Positivo, 0 para Negativo
tweets_minas['Classificacao'] = tweets_minas['Classificacao'].replace(['Positivo', 'Negativo'], [1,0])
tweets_minas.Classificacao.value_counts()

1    3300
0    2446
Name: Classificacao, dtype: int64

In [37]:
# Removendo os valores duplicados:
tweets_minas.drop_duplicates(['Text'], inplace=True)

# Separando tweets e suas classes:
tweets_treino = tweets_minas['Text']
classes = tweets_minas['Classificacao']

In [38]:
#Removendo stopword, links e pontuações dos tweets
def Preprocessing(instancia):
    instancia = re.sub(r"http\S+", "", instancia).lower().replace('.','').replace(';','').replace('-','').replace(':','').replace(')','').replace('"','')
    stopwords = set(nltk.corpus.stopwords.words('portuguese'))
    palavras = [i for i in instancia.split() if not i in stopwords]
    return (" ".join(palavras))

In [39]:
# Aplica a função em todos os dados:
tweets_treino = [Preprocessing(i) for i in tweets_treino]

In [40]:
# Instancia o objeto que faz a vetorização dos dados de texto:
vectorizer = CountVectorizer(analyzer="word", tokenizer=tweet_tokenizer.tokenize)

In [41]:
# Aplica o vetorizador nos dados de texto e retorna uma matriz esparsa
tweets_treino_vetorizados = vectorizer.fit_transform(tweets_treino)

In [42]:
#Instanciando e treinando o modelo
modelo = RandomForestClassifier()
modelo.fit(tweets_treino_vetorizados,classes)

RandomForestClassifier()

In [43]:
#Lendo base de dados de teste
tweets_politica_geral = pd.read_csv('C:/Users/GUILHERME/Desktop/Análise de Sentimentos/Datasets/Classificados/pt2.csv', encoding='utf-8')

In [44]:
# Removendo os valores duplicados:
tweets_politica_geral.drop_duplicates(['Text'], inplace=True)

# Separando tweets e suas classes:
tweets_teste = tweets_politica_geral['Text']

In [45]:
tweets_politica_geral.head()

Text  Classificacao
0         ela vendo a família ( FUGIDINHA VERA LÚCIA              0
1  Eu odeio o fato que muito provavelmente meu vo...              0
2  Ciro mita tanto quanto aquele outro não quero ...              0
3                         Raiva do Bolsonaro agora )              1
4  Reflexos da alienação petista comandada por Lu...              0

In [46]:
# Aplica a limpeza nos dados de teste:
tweets_teste = [Preprocessing(i) for i in tweets_teste]

In [47]:
# Aplica o vetorizador nos dados de texto transformando a lista teste para o modelo bag of words 
tweets_teste_vetorizados = vectorizer.transform(tweets_teste)

In [49]:
#Predição do modelo
classificacao = modelo.predict(tweets_teste_vetorizados)
classificacao

array([1, 1, 1, ..., 1, 1, 1], dtype=int64)

In [50]:
#Contadores para exibição de estatísticas
numPos = 0
numNeg = 0
numNeut = 0
total = 0

In [52]:
# Fazendo a classificação com o modelo treinado:
for tweet, classf in zip (tweets_teste,classificacao):
    #t representa o tweet e c a classificação de cada tweet.
    print ("[TEXTO]" + tweet + "|| [POLARIDADE]: "+ str(classf)) 
    print('\n')
    
    #Estatísticas
    total += 1
    if classf == 1: 
        numPos += 1 
    else:
        numNeg += 1

[TEXTO]vendo família ( fugidinha vera lúcia|| [POLARIDADE]: 1


[TEXTO]odeio fato provavelmente voto vai ter ir pro ciro gomes ( tô triste|| [POLARIDADE]: 1


[TEXTO]ciro mita tanto quanto outro quero ser obrigada votar nele (|| [POLARIDADE]: 1


[TEXTO]raiva bolsonaro agora|| [POLARIDADE]: 1


[TEXTO]reflexos alienação petista comandada lula país maravilhas mundo real lula corrupto inelegível haddad poste manuela sal inexpressiva vice alguém consegue levar brasil sério? (|| [POLARIDADE]: 0


[TEXTO]paulohallier cara to puto pq ciro melhor resposta poderia fazer campanha esquerda super unida pt nessa lula ta vindo ta chegando galera pra chegar hora n conseguir (|| [POLARIDADE]: 0


[TEXTO]cara ciro ficou baqueado pior coisa mundo ser humano sentir chegar ponto fazer umas coisas noção pra sentir alguém importa entendo certa forma ( mtvcatfishbr|| [POLARIDADE]: 1


[TEXTO]cobrador favorito tubo tava falando hoje vai votar bolsonaro ( fiquei mt desapontada|| [POLARIDADE]: 1


[TEXTO]relax

In [53]:
#Sentimento geral
mediaPos = numPos/total
mediaNeg = numNeg/total

In [64]:
#Estatísticas
print('Porcentagem de comentários positivos: '+str(round(mediaPos*100)))
print('Porcentagem de comentários negativos: '+str(round(mediaNeg*100)))
print("\n")
print('Quantidade total de comentários positivos: ' + str(numPos))
print('Quantidade total de comentários negativos: ' + str(numNeg))
if mediaPos > 0.8:
    print("A satisfação com seu produto está satisfatória");
elif mediaPos < mediaNeg:
    print("A satisfação com seu produto está muito baixa");
else:
    print("A satisfação com seu produto está na média");

Porcentagem de comentários positivos: 82
Porcentagem de comentários negativos: 18


Quantidade total de comentários positivos: 50132
Quantidade total de comentários negativos: 11145
A satisfação com seu produto está satisfatória


In [80]:
#Acurácia do modelo
acuracia = accuracy_score(tweets_politica_geral['Classificacao'],classificacao)
print(round((acuracia*100),2),"%")

50.38 %
